# Extraction des informations pour Oralia

In [1]:
import pandas as pd
import numpy as np
import pdfplumber
from pathlib import Path

In [2]:
pdf_file = Path("./pdfs/2022 04 Servient.pdf")
pdf = pdfplumber.open(pdf_file)

In [3]:
xls_charge = f"{pdf_file.stem.replace(' ', '_')}_charge.xlsx"
xls_locataire = f"{pdf_file.stem.replace(' ', '_')}_locataire.xlsx"

## Page 1: Récapitulatif

In [4]:
p1 = pdf.pages[0]

In [5]:
"SITUATION DES LOCATAIRES" in p1.extract_text()

False

##  Situation des locataires

In [6]:
def extract_situation_loc(table):
    df = pd.DataFrame(table[1:], columns=table[0])
    rows = []
    for i, row in df[df["Locataires"]=="Totaux"].iterrows():
        above_row_loc = df.iloc[i-1]["Locataires"]
        up_row = pd.concat([row, 
                            parse_above_loc(above_row_loc),
                           ])

        rows.append(up_row)
    df_cleaned = pd.concat(rows, axis=1).T
    df_cleaned.drop(["Locataires", "", "Période"], axis=1, inplace=True)
    return df_cleaned
    

In [7]:
def parse_above_loc(content):
    row = {}
    try:
        app, loc = content.split("\n")
    except ValueError:
        row["lot"] = ""
        row["type"] = ""
        row["locataire"] = content
        
    else:
        app_ = app.split(" ")
        row["lot"] = app_[1]
        row["type"] = " ".join(app_[2:])
        row["locataire"] = loc
    return pd.Series(row)

In [8]:
p2 = pdf.pages[1]
extract_situation_loc(p2.extract_table())

Loyers Taxes Provisions Divers    Total   Réglés Impayés   lot  \
0    342.80  0.00     663.00   0.00  1005.80  1005.80          0001   
1   3473.79  0.00     519.00  96.79  4089.58  4089.58          0002   
2    597.20  0.00      31.00   0.00   628.60   628.60          0003   
3    596.59  0.00      31.00   0.00   627.59   627.59          0004   
4    468.85  0.00      20.00   0.00   981.03   485.00  496.03  0009   
5    745.39  0.00     191.00   0.00   936.39   936.39          0005   
6    834.55  0.00      81.00   0.00   915.55   915.55          0006   
7    591.69  0.00      50.00   0.00   641.69   641.69                 
8    574.71  0.00      28.00   0.00   602.71   602.71          0008   
9   1201.10  0.00      87.00   0.00  1288.10  1288.10          0010   
10   500.46  0.00      28.00   0.00   528.46   528.46          0011   

               type                                        locataire  
0   Loc. Commercial                                         EFFUSION  
1   Loc. Commercial                                              RAS  
2    Appartement T1                                    KALAI Bernard  
3    Appartement T2                               PEJAUDIER Adelaide  
4    Appartement T1                                   MANNA Baptiste  
5   Loc. Commercial                             ATELIERS RENAISSANCE  
6    Appartement T3                                  GUELLIER MURIEL  
7                    Lot 0007 Appartement T1\nDOMINIKIEWICZ\nMELANIE  
8    Appartement T1                                       BESSON Léa  
9    Appartement T3                                FILIPPI Bérengère  
10   Appartement T1                                      LOINE Anaïs

In [9]:
charge_table_settings = {
    "vertical_strategy": "lines",
    "horizontal_strategy": "text",
}
def extract_charge(table):
    df = pd.DataFrame(table[1:], columns=table[0]).replace("", np.nan).dropna(subset=["Débits"])
    drop_index = df[df["RECAPITULATIF DES OPERATIONS"].str.contains("TOTAUX", case=False)].index
    df.drop(drop_index, inplace=True)
    return df

In [10]:
p4 = pdf.pages[3]
extract_charge(p4.extract_table(charge_table_settings))

RECAPITULATIF DES OPERATIONS  Débits  \
4       DIDIER NETTOYAGE                PC - ENTRETIEN IMMEUBLE  708.58   
6   TOTAL DIRECT ENERGIE                PC TOTAL DIRECT ENERGIE   65.70   
7                    EDF                   PC EDF DU 17.04.2022   89.56   
9         PICARD SERVICE                  Facture du 11/04/2022   66.76   
15       V2C MAINTENANCE  6 - remplacement circulateur chudière  447.70   
20           IMI GERANCE                    TAVARES NORTE Dylan   93.00   
23           IMI GERANCE                    TAVARES NORTE Dylan  173.58   
27           IMI GERANCE                    TAVARES NORTE Dylan  798.72   
29                   NaN                        Honoraires H.T.  979.20   
30                   NaN             TVA/Honoraires ( 20.00 % )  195.84   

   Crédits Dont T.V.A. Locatif Déductible  
4      NaN      118.10  708.58        NaN  
6      NaN        7.03   65.70        NaN  
7      NaN       10.22   89.56        NaN  
9      NaN        6.07   66.76        NaN  
15     NaN       40.70     NaN     447.70  
20     NaN       15.50     NaN      93.00  
23     NaN       28.93     NaN     173.58  
27     NaN      133.12     NaN     798.72  
29     NaN         NaN     NaN     979.20  
30     NaN      195.84     NaN     195.84

In [11]:
# im = p4.to_image()
# im.debug_tablefinder(charge_table_settings)

In [12]:
frames = []
loc_table = []
for page in pdf.pages:
    situation_loc_line = [l for l in page.extract_text().split("\n") if "SITUATION DES LOCATAIRES CRG" in l]
    if situation_loc_line:
        mois, annee = situation_loc_line[0].split(" ")[-2:]
        if loc_table:
            loc_table += page.extract_table()[1:]
        else:
            loc_table = page.extract_table()

    if "HONORAIRES" in page.extract_text():
        df_charge = extract_charge(page.extract_table(charge_table_settings))

        df_charge.to_excel(xls_charge, sheet_name="Charges", index=False)


df_loc = extract_situation_loc(loc_table)
df_loc = df_loc.assign(
    mois = mois,
    annee = annee
)
df_loc.to_excel(xls_locataire, sheet_name="Location", index=False)
#df_loc

ModuleNotFoundError: No module named 'openpyxl'